In [1]:
import pandas as pd
import numpy as np

from sklearn import datasets
from sklearn.linear_model import Ridge
from sklearn.linear_model import BayesianRidge
from sklearn.metrics import r2_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler

import keras
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasRegressor

In [2]:
# SELECCIÓN DEL MODELO Y ENTRENAMIENTO

# Lectura del dataset

dataset = pd.read_csv('C:/Users/toled/OneDrive/Documentos/MATEMÁTICAS/TFG/Dataset NBA.csv',sep=";", encoding="ISO 8859-1")
dataset = dataset.drop('YEAR', 1)
dataset = dataset.drop('Team', 1)
dataset = dataset.drop('Arena', 1)
dataset = dataset.drop('Champion', 1)
dataset = dataset.drop('Attend.', 1)
dataset = dataset.drop('L%', 1)
dataset = dataset.drop('PW', 1)
dataset = dataset.drop('PL', 1)

dataset.head()

C:\Users\toled\AppData\Local\Temp/ipykernel_9668/1573650165.py:6: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('YEAR', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_9668/1573650165.py:7: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Team', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_9668/1573650165.py:8: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Arena', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_9668/1573650165.py:9: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Champion', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_9668/1573650165.py:

G     MP    FG   FGA   FG%    3P   3PA   3P%    2P   2PA  ...  3PAr   TS%  \
0  82  240.3  41.5  88.3  47.0  12.9  34.4  37.4  28.6  53.9  ...   390  58.1   
1  82  240.6  41.7  85.6  48.7   1.5   5.0  30.2  40.2  80.6  ...    59  54.7   
2  82  242.7  42.6  91.2  46.7   2.6   8.2  31.3  40.0  83.0  ...    90  51.9   
3  82  242.7  34.9  78.5  44.4   4.9  13.9  35.2  30.0  64.5  ...   177  52.7   
4  82  242.1  42.0  86.8  48.4   0.9   2.9  31.1  41.1  84.0  ...    33  53.6   

   OFeFG%  OfTOV%  ORB%  Of FT/FGA  DEFeFG%  DefTOV%  DRB%  Def FT/FGA  
0    54.3    10.8  23.0        205     54.3     11.5  76.9         177  
1    49.6    13.5  36.3        277     50.9     14.0  65.5         254  
2    48.1    13.0  33.6        203     49.7     13.2  68.3         209  
3    47.6    15.7  27.9        248     46.9     12.1  70.4         222  
4    48.9    15.3  32.5        250     48.5     15.2  63.8         249  

[5 rows x 42 columns]

In [3]:
# Preprocesado

# Se separa la columna a predecir
X = dataset.iloc[:,dataset.columns != 'W%']
y = dataset.iloc[:,25]

# En este ejemplo, se reescalan con un MinMaxScaler
sc = MinMaxScaler()
sc.fit(X) # Se ajusta el reescalador
X = sc.transform(X)

print(X)
print(y)

[[1.         0.06122449 0.60451977 ... 0.13793103 0.76616915 0.10526316]
 [1.         0.12244898 0.61581921 ... 0.42528736 0.19900498 0.51052632]
 [1.         0.55102041 0.66666667 ... 0.33333333 0.33830846 0.27368421]
 ...
 [1.         0.36734694 0.31073446 ... 0.55172414 0.46766169 0.52105263]
 [1.         0.36734694 0.37288136 ... 0.47126437 0.47263682 0.48421053]
 [0.6875     0.34693878 0.70056497 ... 0.25287356 0.80099502 0.31578947]]
0       0.524390
1       0.500000
2       0.463415
3       0.426829
4       0.414634
          ...   
1189    0.524390
1190    0.524390
1191    0.512195
1192    0.500000
1193    0.472222
Name: W%, Length: 1194, dtype: float64


In [4]:
# Dividir el dataset en train y test

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33)

In [5]:
# SELECCION DE HIPERPARAMETROS POR VALIDACION CRUZADA

# Modelo: Bayesian Ridge

parameters = {'n_iter':[100, 200, 300, 500],\
              'alpha_1':[1e-6, 1e-4, 1e-1, 1], \
              'alpha_2':[1e-4, 1e-10, 1e-1, 1], \
              'lambda_1':[1e-6, 1e-10, 1e-1, 1],\
              'lambda_2':[1e-6, 1e-4]}

bay_ridge = BayesianRidge()
cv = GridSearchCV(bay_ridge, parameters, refit = True, scoring='r2', verbose = 3)
cv.fit(X_train, y_train)

Fitting 5 folds for each of 512 candidates, totalling 2560 fits
[CV 1/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.940 total time=   0.0s
[CV 2/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.942 total time=   0.0s
[CV 3/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.941 total time=   0.0s
[CV 4/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.928 total time=   0.0s
[CV 5/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.945 total time=   0.0s
[CV 1/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0.940 total time=   0.0s
[CV 2/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0.942 total time=   0.0s
[CV 3/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0

GridSearchCV(estimator=BayesianRidge(),
             param_grid={'alpha_1': [1e-06, 0.0001, 0.1, 1],
                         'alpha_2': [0.0001, 1e-10, 0.1, 1],
                         'lambda_1': [1e-06, 1e-10, 0.1, 1],
                         'lambda_2': [1e-06, 0.0001],
                         'n_iter': [100, 200, 300, 500]},
             scoring='r2', verbose=3)

In [6]:
# Mostrar el ranking

pd.DataFrame(cv.cv_results_).sort_values(by=['rank_test_score']).head()

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
428       0.003601      0.000490         0.000200         0.00040   
429       0.003600      0.000490         0.000400         0.00049   
430       0.003801      0.000749         0.000600         0.00049   
431       0.003801      0.000749         0.000400         0.00049   
423       0.003419      0.000477         0.000622         0.00037   

    param_alpha_1 param_alpha_2 param_lambda_1 param_lambda_2 param_n_iter  \
428             1           0.0            0.0         0.0001          100   
429             1           0.0            0.0         0.0001          200   
430             1           0.0            0.0         0.0001          300   
431             1           0.0            0.0         0.0001          500   
423             1           0.0       0.000001         0.0001          500   

                                                params  split0_test_score  \
428  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.940022   
429  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.940022   
430  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.940022   
431  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.940022   
423  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.940022   

     split1_test_score  split2_test_score  split3_test_score  \
428           0.942304           0.940654           0.928307   
429           0.942304           0.940654           0.928307   
430           0.942304           0.940654           0.928307   
431           0.942304           0.940654           0.928307   
423           0.942304           0.940654           0.928307   

     split4_test_score  mean_test_score  std_test_score  rank_test_score  
428           0.944516         0.939161        0.005645                1  
429           0.944516         0.939161        0.005645                1  
430           0.944516         0.939161        0.005645                1  
431           0.944516         0.939161        0.005645                1  
423           0.944516         0.939161        0.005645                5

In [40]:
# Modelo: Red neuronal

def neural_network(neuronas_capa_1 = 25, neuronas_capa_2 = 15):
    neural_net = Sequential()
    neural_net.add(Dense(neuronas_capa_1, input_dim=X.shape[1], activation='sigmoid'))
    neural_net.add(Dense(neuronas_capa_2, activation='sigmoid'))
    neural_net.add(Dense(1, activation='linear'))

    neural_net.compile(loss='mean_squared_error', optimizer='adam', metrics=['mae'])
    return neural_net

neu_net = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[25, 50, 10], 'neuronas_capa_2':[25, 50, 10], 'batch_size':[20, 30]}

cv = GridSearchCV(neu_net, parameters, refit=True, scoring='r2', verbose= 3)
cv.fit(X_train, y_train)

Fitting 5 folds for each of 18 candidates, totalling 90 fits
Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/1291393717.py:12: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net = KerasRegressor(build_fn=neural_network, epochs = 500)


32/32 [==============================] - 0s 1ms/step - loss: 0.1660 - mae: 0.3238
Epoch 2/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0258 - mae: 0.1307
Epoch 3/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0220 - mae: 0.1227
Epoch 4/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0209 - mae: 0.1195
Epoch 5/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0201 - mae: 0.1172
Epoch 6/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0190 - mae: 0.1140
Epoch 7/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0180 - mae: 0.1102
Epoch 8/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0169 - mae: 0.1070
Epoch 9/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0157 - mae: 0.1034
Epoch 10/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0145 - mae: 0.0988
Epoch 11/500
32/32 [==============================] - 0s 1ms/step - los

GridSearchCV(estimator=<keras.wrappers.scikit_learn.KerasRegressor object at 0x00000230B6A31A90>,
             param_grid={'batch_size': [20, 30],
                         'neuronas_capa_1': [25, 50, 10],
                         'neuronas_capa_2': [25, 50, 10]},
             scoring='r2', verbose=3)

In [41]:
# Mostrar el ranking

pd.DataFrame(cv.cv_results_).sort_values(by=['rank_test_score']).head()

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
8       27.254899      0.651165         0.073110        0.004433   
2       26.143814      0.706660         0.075193        0.009649   
14      16.223242      0.800936         0.073653        0.002862   
7       26.506085      1.116249         0.085565        0.009703   
16      15.752270      0.267792         0.071719        0.007347   

   param_batch_size param_neuronas_capa_1 param_neuronas_capa_2  \
8                20                    10                    10   
2                20                    25                    10   
14               30                    50                    10   
7                20                    10                    50   
16               30                    10                    50   

                                               params  split0_test_score  \
8   {'batch_size': 20, 'neuronas_capa_1': 10, 'neu...           0.943616   
2   {'batch_size': 20, 'neuronas_capa_1': 25, 'neu...           0.942627   
14  {'batch_size': 30, 'neuronas_capa_1': 50, 'neu...           0.942342   
7   {'batch_size': 20, 'neuronas_capa_1': 10, 'neu...           0.945457   
16  {'batch_size': 30, 'neuronas_capa_1': 10, 'neu...           0.944759   

    split1_test_score  split2_test_score  split3_test_score  \
8            0.937185           0.933884           0.936755   
2            0.937551           0.933564           0.933412   
14           0.934540           0.933083           0.937974   
7            0.930442           0.934075           0.934423   
16           0.928110           0.934272           0.936783   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
8            0.952906         0.940869        0.006808                1  
2            0.952249         0.939880        0.007038                2  
14           0.951430         0.939874        0.006600                3  
7            0.953330         0.939545        0.008532                4  
16           0.951462         0.939077        0.008177                5

In [47]:
#Mejor modelo

neu_net1 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[10], 'batch_size':[20]}

neu_net1.fit(X_train, y_train)

ml_model1 = neu_net1

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/3547059292.py:1: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net1 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 1s 1ms/step - loss: 1.2678 - mae: 1.1009
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.3410 - mae: 0.5476
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0679 - mae: 0.2212
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0236 - mae: 0.1287
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0205 - mae: 0.1196
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0204 - mae: 0.1190
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0202 - mae: 0.1186
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0200 - mae: 0.1179
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0198 - mae: 0.1171
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0196 - mae: 0.1166
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [48]:
# Predecir en test

y_pred1 = ml_model1.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred1)))

R2 obtenido en test: 0.9466568321498269


In [49]:
#Segundo mejor modelo

neu_net2 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[25], 'neuronas_capa_2':[10], 'batch_size':[20]}

neu_net2.fit(X_train, y_train)

ml_model2 = neu_net2

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/4188163804.py:1: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net2 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 2ms/step - loss: 0.2933 - mae: 0.4885
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0276 - mae: 0.1343
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0236 - mae: 0.1256
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0215 - mae: 0.1223
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0209 - mae: 0.1200
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0203 - mae: 0.1184
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0197 - mae: 0.1165
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0190 - mae: 0.1147
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0182 - mae: 0.1121
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0174 - mae: 0.1097
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [57]:
# Predecir en test

y_pred2 = ml_model2.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred2)))

R2 obtenido en test: 0.9408736171377546


In [58]:
#Tercer mejor modelo

neu_net3 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[50], 'neuronas_capa_2':[10], 'batch_size':[30]}

neu_net3.fit(X_train, y_train)

ml_model3 = neu_net3

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/3844175911.py:1: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net3 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 0.0556 - mae: 0.1873
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0224 - mae: 0.1225
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0195 - mae: 0.1152
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0179 - mae: 0.1108
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0164 - mae: 0.1060
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0148 - mae: 0.1003
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0132 - mae: 0.0944
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0116 - mae: 0.0883
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0099 - mae: 0.0815
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0083 - mae: 0.0742
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [59]:
# Predecir en test

y_pred3 = ml_model3.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred3)))

R2 obtenido en test: 0.9360247968259111


In [60]:
#Cuarto mejor modelo

neu_net4 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[50], 'batch_size':[20]}

neu_net4.fit(X_train, y_train)

ml_model4 = neu_net4

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/2560579874.py:1: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net4 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 0.4539 - mae: 0.6172
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0281 - mae: 0.1362
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0205 - mae: 0.1157
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0182 - mae: 0.1125
Epoch 5/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0177 - mae: 0.1105
Epoch 6/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0171 - mae: 0.1088
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0166 - mae: 0.1066
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0159 - mae: 0.1048
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0153 - mae: 0.1028
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0147 - mae: 0.1007
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [61]:
# Predecir en test

y_pred4 = ml_model4.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred4)))

R2 obtenido en test: 0.9451761618949417


In [62]:
#Quinto mejor modelo

neu_net5 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[50], 'batch_size':[30]}

neu_net5.fit(X_train, y_train)

ml_model5 = neu_net5

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_1092/3127724397.py:1: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net5 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 1.5780 - mae: 1.2287
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.3942 - mae: 0.5914
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0651 - mae: 0.2139
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0211 - mae: 0.1218
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0196 - mae: 0.1159
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0194 - mae: 0.1153
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0191 - mae: 0.1148
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0189 - mae: 0.1141
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0187 - mae: 0.1137
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0184 - mae: 0.1125
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [63]:
# Predecir en test

y_pred5 = ml_model5.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred5)))

R2 obtenido en test: 0.9448378282893131
